# INDEX
* [Functions](#Functions)
* [Configuration](#Configuration)
* [Preprocess training data](#Preprocess-training-data)
* [Train](#Train)
* [Test model](#Test-model)
    * [Predict](#Predict)
    * [Explore dataset](#Explore-dataset)

# Prerequisites

* go to parent root folder of off-category-classification
* execute download.sh

# Functions

In [1]:
import sys
sys.path.append('../') #append a relative path to the top package to the search path

In [2]:
# %load libtrain.py
import datetime
import functools
import json
import pathlib
import shutil
import tempfile
from typing import Dict, List

import dacite
import pandas as pd
import tensorflow as tf
from robotoff.taxonomy import Taxonomy
from tensorflow import keras
from tensorflow.data import Dataset
from tensorflow.keras import callbacks
from tensorflow.python.ops import summary_ops_v2

import settings
from category_classification.data_utils import (
    TFTransformer,
    create_tf_dataset,
    load_dataframe,
)
from category_classification.models import (
    KerasPreprocessing,
    build_model,
    construct_preprocessing,
    to_serving_model,
)

from category_classification.config import Config

from utils.io import (
    copy_category_taxonomy,
    save_category_vocabulary,
    save_config,
    save_json,
)
from utils.metrics import evaluation_report

def create_model(config: Config, preprocess: KerasPreprocessing) -> keras.Model:
    model = build_model(config.model_config, preprocess)
    loss_fn = keras.losses.BinaryCrossentropy(
        label_smoothing=config.train_config.label_smoothing
    )
    optimizer = keras.optimizers.Adam(learning_rate=config.train_config.lr)
    model.compile(
        optimizer=optimizer,
        loss=loss_fn,
        metrics=["binary_accuracy", "Precision", "Recall"],
    )
    return model


class TBCallback(callbacks.TensorBoard):
    """Get around a bug where you cannot use the TensorBoard callback with the StringLookup layers
    - https://github.com/tensorflow/tensorboard/issues/4530#issuecomment-783318292"""

    def _log_weights(self, epoch):
        with self._train_writer.as_default():
            with summary_ops_v2.always_record_summaries():
                for layer in self.model.layers:
                    for weight in layer.weights:
                        if hasattr(weight, "name"):
                            weight_name = weight.name.replace(":", "_")
                            summary_ops_v2.histogram(weight_name, weight, step=epoch)
                            if self.write_images:
                                self._log_weight_as_image(weight, weight_name, epoch)
                self._train_writer.flush()


def train(
    model: keras.Model,
    save_dir: pathlib.Path,
    config: Config,
    category_vocab: List[str],
):
    print("Starting training...")
    temporary_log_dir = pathlib.Path(tempfile.mkdtemp())
    print("Temporary log directory: {}".format(temporary_log_dir))

    tf_transformer = TFTransformer(category_vocab)

    train = create_tf_dataset("train", config.train_config.batch_size, tf_transformer)
    val = create_tf_dataset("val", config.train_config.batch_size, tf_transformer)

    history=model.fit(train,
        epochs= config.train_config.epochs,
        validation_data=val,
        callbacks=[
            callbacks.TerminateOnNaN(),
            callbacks.ModelCheckpoint(
                filepath=str(save_dir / "weights.{epoch:02d}-{val_loss:.4f}"),
                monitor="val_loss",
                save_best_only=True,
                save_format='tf',
            ),
            #TBCallback(log_dir=str(temporary_log_dir), histogram_freq=1),
            callbacks.EarlyStopping(monitor="val_loss", patience=4),
            #callbacks.CSVLogger(str(save_dir / "training.csv")),
            callbacks.History()
        ],
    )
    print("Training ended")
    return history


# Configuration

In [3]:
# load config json
import json
 
# Opening JSON file
with open('../config.json') as json_file:
    json_config = json.load(json_file)
json_config 

config=dacite.from_dict(Config, json_config)
model_config=config.model_config

output_dir:pathlib.Path = pathlib.Path("../models")
replicates = 1

output_dir.mkdir(parents=True, exist_ok=True)

# Preprocess training data

In [4]:
%%time
keras_preprocess = construct_preprocessing(
    model_config.category_min_count,
    model_config.ingredient_min_count,
    model_config.product_name_max_tokens,
    model_config.product_name_max_length,
    load_dataframe("train"),
)
print("Pre-processed training data")

2022-04-09 10:19:56.039481: I tensorflow/core/platform/cpu_feature_guard.cc:142] This TensorFlow binary is optimized with oneAPI Deep Neural Network Library (oneDNN) to use the following CPU instructions in performance-critical operations:  AVX2 FMA
To enable them in other operations, rebuild TensorFlow with the appropriate compiler flags.
2022-04-09 10:19:56.187669: I tensorflow/compiler/mlir/mlir_graph_optimization_pass.cc:185] None of the MLIR Optimization Passes are enabled (registered 2)


Pre-processed training data
CPU times: user 4min 56s, sys: 2.88 s, total: 4min 59s
Wall time: 4min 45s


# Train

In [7]:
%%time
import json

if replicates == 1:
    save_dirs = [output_dir]
else:
    save_dirs = [output_dir / str(i) for i in range(replicates)]

for i, save_dir in enumerate(save_dirs):
    model = create_model(config, keras_preprocess)
    save_dir.mkdir(exist_ok=True)
    config.train_config.start_datetime = str(datetime.datetime.utcnow())
    print(f"Starting training repeat {i}")

    save_config(config, save_dir)
    copy_category_taxonomy(settings.CATEGORY_TAXONOMY_PATH, save_dir)
    save_category_vocabulary(keras_preprocess.category_vocab, save_dir)
    # Get the dictionary containing each metric and the loss for each epoch
    history=train(
        model,
        save_dir,
        config,
        keras_preprocess.category_vocab,
    )

    config.train_config.end_datetime = str(datetime.datetime.utcnow())
    save_config(config, save_dir)
    config.train_config.start_datetime = None
    config.train_config.end_datetime = None

Starting training repeat 0
Starting training...
Temporary log directory: /var/folders/c7/w4lf4cp91_j_p3dxm9w00rmh0000gn/T/tmp2o2lcebx
Epoch 1/50
5465/5465 [==============================] - 1408s 257ms/step - loss: 0.0081 - binary_accuracy: 0.9985 - precision: 0.2376 - recall: 0.0929 - val_loss: 0.0040 - val_binary_accuracy: 0.9990 - val_precision: 0.8507 - val_recall: 0.2642
INFO:tensorflow:Assets written to: models/weights.01-0.0040/assets
Epoch 2/50
5465/5465 [==============================] - 1451s 265ms/step - loss: 0.0033 - binary_accuracy: 0.9992 - precision: 0.8171 - recall: 0.4194 - val_loss: 0.0023 - val_binary_accuracy: 0.9994 - val_precision: 0.8848 - val_recall: 0.5584
INFO:tensorflow:Assets written to: models/weights.02-0.0023/assets
Epoch 3/50
5465/5465 [==============================] - 3169s 580ms/step - loss: 0.0022 - binary_accuracy: 0.9994 - precision: 0.8460 - recall: 0.5942 - val_loss: 0.0018 - val_binary_accuracy: 0.9995 - val_precision: 0.8872 - val_recall: 0.66

In [ ]:
json.dump(history, open(./models/history.json, 'w'))
#history_dict = json.load(open(your_history_path, 'r'))

In [ ]:
import matplotlib.pyplot as plt

plt.plot(history.history['binary_accuracy'])
plt.plot(history.history['val_binary_accuracy'])
plt.title('Model categories_tags~product_name+ingredient_tags')
plt.ylabel('MSE')
plt.xlabel('iterations')
plt.legend(['train' , 'validation'] , loc = 'upper right')
plt.show()

# Test model

In [5]:
# load saved model
model=keras.models.load_model('../models/base/saved_model')

In [6]:
category_vocab=keras_preprocess.category_vocab
tf_transformer = TFTransformer(category_vocab)

# Train & validation Dataset => investigate on characteristics of the source
traindata = create_tf_dataset("train", config.train_config.batch_size, tf_transformer)
valdata = create_tf_dataset("val", config.train_config.batch_size, tf_transformer)
testdata = create_tf_dataset("test", config.train_config.batch_size, tf_transformer)


In [7]:
len(category_vocab)

3969

## Predict

In [8]:
%%time
y_pred_val = model.predict(valdata)

CPU times: user 1min 34s, sys: 15.7 s, total: 1min 49s
Wall time: 1min 19s


In [9]:
%%time
y_pred_test=model.predict(testdata)

CPU times: user 1min 35s, sys: 16 s, total: 1min 51s
Wall time: 1min 20s


In [10]:
y_pred_val.shape, y_pred_test.shape

((87434, 3969), (87434, 3969))

In [11]:
y_pred_val

array([[1.2839634e-05, 2.3829339e-10, 1.6613468e-09, ..., 1.5564917e-11,
        3.6129602e-10, 2.1100532e-12],
       [1.0495579e-01, 2.0508166e-09, 2.3943665e-09, ..., 1.3911613e-08,
        1.0217517e-08, 3.8321792e-07],
       [1.9471225e-05, 6.9090309e-14, 3.4578873e-15, ..., 1.7461139e-10,
        1.5341870e-09, 3.1657670e-11],
       ...,
       [3.8076937e-03, 1.6157297e-06, 6.6229504e-06, ..., 1.5495643e-06,
        8.5407401e-06, 3.0552085e-06],
       [1.3194382e-03, 1.6692168e-10, 3.1451568e-09, ..., 4.1883336e-14,
        4.0008542e-17, 5.4479357e-14],
       [1.3995171e-04, 4.6972590e-09, 6.7628537e-07, ..., 2.1551901e-16,
        4.0634002e-10, 5.0259403e-15]], dtype=float32)

### Translate prediction array

In [25]:
# test data predictions
import numpy as np
argmaxes=np.argmax(y_pred_test ,axis=1)

r=0
for i in argmaxes:
    print(f'row:{r} - {category_vocab[i]} - {round(y_pred_test[r,i]*100,2)}%')
    r+=1

row:0 - en:sausages - 34.16%
row:1 - en:sauces - 99.47%
row:2 - en:snacks - 97.94%
row:3 - en:beverages - 96.49%
row:4 - en:cheeses - 93.3%
row:5 - en:snacks - 99.51%
row:6 - en:plant-based-foods-and-beverages - 99.94%
row:7 - en:plant-based-foods-and-beverages - 98.53%
row:8 - en:meals - 84.33%
row:9 - en:snacks - 92.14%
row:10 - en:dairies - 93.81%
row:11 - en:fermented-foods - 99.64%
row:12 - en:beverages - 99.99%
row:13 - en:sauces - 97.58%
row:14 - en:eggs - 97.86%
row:15 - en:sauces - 95.85%
row:16 - en:milk-substitute - 99.31%
row:17 - en:snacks - 94.92%
row:18 - en:beverages - 99.43%
row:19 - en:biscuits - 98.97%
row:20 - en:beverages - 96.61%
row:21 - en:plant-based-foods-and-beverages - 75.1%
row:22 - en:plant-based-foods-and-beverages - 98.1%
row:23 - en:meats - 99.34%
row:24 - en:plant-based-foods - 97.0%
row:25 - en:fishes - 96.17%
row:26 - en:meals - 87.75%
row:27 - en:snacks - 77.07%
row:28 - en:snacks - 89.67%
row:29 - en:plant-based-foods - 95.5%
row:30 - en:fruits-and

row:1549 - en:snacks - 77.86%
row:1550 - en:fish-soups - 98.82%
row:1551 - en:snacks - 95.88%
row:1552 - en:plant-based-foods-and-beverages - 93.78%
row:1553 - en:beverages - 98.71%
row:1554 - en:aligots - 95.84%
row:1555 - en:meats - 99.37%
row:1556 - en:beverages - 99.15%
row:1557 - en:sodas - 99.77%
row:1558 - en:snacks - 97.9%
row:1559 - en:snacks - 99.78%
row:1560 - en:cocoa-and-its-products - 76.44%
row:1561 - en:seafood - 88.23%
row:1562 - en:meats - 95.76%
row:1563 - en:beverages - 99.51%
row:1564 - en:dairies - 97.57%
row:1565 - en:fats - 79.68%
row:1566 - en:beverages - 99.61%
row:1567 - en:beverages - 99.74%
row:1568 - en:fried-tomato-sauces - 98.4%
row:1569 - en:plant-based-foods-and-beverages - 99.61%
row:1570 - en:seafood - 99.56%
row:1571 - en:biscuits-and-cakes - 92.85%
row:1572 - en:meats - 100.0%
row:1573 - en:snacks - 99.31%
row:1574 - en:fruits-and-vegetables-based-foods - 73.38%
row:1575 - en:spreads - 57.76%
row:1576 - en:fermented-foods - 99.25%
row:1577 - en:fat

row:3272 - en:ground-meat-preparations - 82.78%
row:3273 - en:snacks - 93.03%
row:3274 - en:biscuits - 98.92%
row:3275 - en:dairies - 98.93%
row:3276 - en:plant-based-foods-and-beverages - 91.65%
row:3277 - en:frozen-desserts - 99.74%
row:3278 - en:biscuits-and-cakes - 89.86%
row:3279 - en:groceries - 99.86%
row:3280 - en:vinegars - 88.53%
row:3281 - en:sauces - 98.85%
row:3282 - en:biscuits-and-cakes - 98.9%
row:3283 - en:biscuits-and-cakes - 98.3%
row:3284 - en:beverages - 88.41%
row:3285 - en:beverages - 92.75%
row:3286 - en:yeast - 93.49%
row:3287 - en:plant-based-foods-and-beverages - 94.47%
row:3288 - en:frozen-foods - 91.69%
row:3289 - en:meals - 96.04%
row:3290 - en:beverages - 95.91%
row:3291 - en:frozen-desserts - 99.86%
row:3292 - en:meals - 48.78%
row:3293 - en:frozen-foods - 34.37%
row:3294 - en:cakes - 76.62%
row:3295 - en:plant-based-foods - 98.88%
row:3296 - en:meats - 99.94%
row:3297 - en:snacks - 92.7%
row:3298 - en:plant-based-foods-and-beverages - 97.64%
row:3299 - 

row:4548 - en:fermented-foods - 95.92%
row:4549 - en:plant-based-foods-and-beverages - 99.94%
row:4550 - en:plant-based-foods - 50.59%
row:4551 - en:plant-based-foods - 79.99%
row:4552 - en:desserts - 95.22%
row:4553 - en:frozen-desserts - 99.99%
row:4554 - en:dairies - 99.89%
row:4555 - en:meals - 95.5%
row:4556 - en:snacks - 90.92%
row:4557 - en:beverages - 97.1%
row:4558 - en:frozen-foods - 67.75%
row:4559 - en:dairies - 99.9%
row:4560 - en:snacks - 97.71%
row:4561 - en:snacks - 95.78%
row:4562 - en:sauces - 99.89%
row:4563 - en:snacks - 97.83%
row:4564 - en:biscuits - 98.63%
row:4565 - en:breakfasts - 99.61%
row:4566 - en:sweet-snacks - 98.35%
row:4567 - en:beverages - 99.99%
row:4568 - en:plant-based-foods - 86.41%
row:4569 - en:dairies - 99.18%
row:4570 - en:breakfast-cereals - 84.01%
row:4571 - en:biscuits-and-cakes - 68.83%
row:4572 - en:sauces - 99.84%
row:4573 - en:snacks - 89.2%
row:4574 - en:plant-based-foods-and-beverages - 99.72%
row:4575 - en:snacks - 97.26%
row:4576 - e

row:6047 - en:fats - 68.14%
row:6048 - en:fermented-foods - 99.6%
row:6049 - en:tartlets - 90.13%
row:6050 - en:plant-based-foods-and-beverages - 94.3%
row:6051 - en:rillettes - 99.57%
row:6052 - en:meats - 99.89%
row:6053 - en:plant-based-foods-and-beverages - 95.0%
row:6054 - en:snacks - 98.72%
row:6055 - en:cereals-and-their-products - 54.47%
row:6056 - en:seafood - 96.56%
row:6057 - en:snacks - 74.23%
row:6058 - en:snacks - 99.74%
row:6059 - en:plant-based-foods-and-beverages - 80.4%
row:6060 - en:meats - 99.23%
row:6061 - en:foies-gras - 87.92%
row:6062 - en:plant-based-foods-and-beverages - 98.05%
row:6063 - en:dairies - 99.91%
row:6064 - en:beverages - 99.72%
row:6065 - en:dairies - 99.85%
row:6066 - en:plant-based-foods-and-beverages - 98.05%
row:6067 - en:beverages - 92.73%
row:6068 - en:seafood - 99.65%
row:6069 - en:plant-based-foods-and-beverages - 78.75%
row:6070 - en:fats - 97.53%
row:6071 - en:plant-based-foods-and-beverages - 93.31%
row:6072 - en:snacks - 98.96%
row:607

...

row:79960 - en:foies-gras - 99.66%
row:79961 - en:seeds - 91.29%
row:79962 - en:meats - 95.87%
row:79963 - en:dairies - 99.24%
row:79964 - en:snacks - 98.88%
row:79965 - en:meats - 99.9%
row:79966 - en:meals - 87.36%
row:79967 - en:snacks - 97.24%
row:79968 - en:fermented-foods - 96.78%
row:79969 - en:snacks - 93.06%
row:79970 - en:snacks - 98.2%
row:79971 - en:snacks - 99.77%
row:79972 - en:chestnut-yogurts - 75.36%
row:79973 - en:snacks - 77.88%
row:79974 - en:plant-based-foods-and-beverages - 86.23%
row:79975 - en:sweet-spreads - 99.28%
row:79976 - en:seafood - 96.93%
row:79977 - en:terrines - 97.45%
row:79978 - en:beverages - 64.34%
row:79979 - en:compotes - 94.45%
row:79980 - en:plant-based-foods-and-beverages - 98.73%
row:79981 - en:desserts - 70.34%
row:79982 - en:sweeteners - 97.82%
row:79983 - en:seafood - 94.8%
row:79984 - en:plant-based-foods-and-beverages - 99.74%
row:79985 - en:fruits-and-vegetables-based-foods - 97.02%
row:79986 - en:dairies - 99.99%
row:79987 - en:snacks

row:81526 - en:meats - 89.24%
row:81527 - en:meals - 29.95%
row:81528 - en:confectioneries - 99.98%
row:81529 - en:snacks - 98.71%
row:81530 - en:beverages - 73.58%
row:81531 - en:snacks - 99.7%
row:81532 - en:plant-based-foods-and-beverages - 100.0%
row:81533 - en:fats - 68.77%
row:81534 - en:fermented-milk-products - 100.0%
row:81535 - en:sweet-snacks - 85.54%
row:81536 - en:snacks - 99.49%
row:81537 - en:non-dairy-desserts - 97.06%
row:81538 - en:snacks - 87.61%
row:81539 - en:snacks - 99.73%
row:81540 - en:bee-products - 99.91%
row:81541 - en:meats - 97.17%
row:81542 - en:eggs - 99.95%
row:81543 - en:pizzas-pies-and-quiches - 97.58%
row:81544 - en:snacks - 97.19%
row:81545 - en:dairies - 46.71%
row:81546 - en:snacks - 78.65%
row:81547 - en:meals - 98.46%
row:81548 - en:herbal-teas - 90.9%
row:81549 - en:milks - 90.08%
row:81550 - en:plant-based-foods-and-beverages - 98.83%
row:81551 - en:beverages - 99.66%
row:81552 - en:frozen-desserts - 98.25%
row:81553 - en:plant-based-foods-and

row:83382 - en:plant-based-foods-and-beverages - 99.69%
row:83383 - en:snacks - 99.24%
row:83384 - en:snacks - 90.63%
row:83385 - en:seafood - 99.62%
row:83386 - en:sweet-snacks - 82.83%
row:83387 - en:cheeses - 99.76%
row:83388 - en:meals - 95.22%
row:83389 - en:seafood - 99.79%
row:83390 - en:beverages - 99.61%
row:83391 - en:seafood - 99.15%
row:83392 - en:plant-based-foods-and-beverages - 92.75%
row:83393 - en:snacks - 92.29%
row:83394 - en:sweeteners - 96.41%
row:83395 - en:snacks - 52.17%
row:83396 - en:plant-based-foods-and-beverages - 95.37%
row:83397 - en:dairies - 91.05%
row:83398 - en:beverages - 95.99%
row:83399 - en:fishes - 86.11%
row:83400 - en:rices - 99.41%
row:83401 - en:meats - 81.88%
row:83402 - en:breads - 66.21%
row:83403 - en:meats - 99.04%
row:83404 - en:meals - 64.36%
row:83405 - en:plant-based-foods-and-beverages - 99.79%
row:83406 - en:snacks - 89.66%
row:83407 - en:meats - 99.68%
row:83408 - en:beverages - 99.77%
row:83409 - en:plant-based-foods-and-beverage

row:85025 - en:legumes-and-their-products - 97.92%
row:85026 - en:meals - 94.9%
row:85027 - en:biscuits-and-cakes - 93.87%
row:85028 - en:sauces - 99.36%
row:85029 - en:groceries - 99.6%
row:85030 - en:stuffed-pastas - 90.52%
row:85031 - en:sandwiches - 34.72%
row:85032 - en:fermented-foods - 99.89%
row:85033 - en:snacks - 99.99%
row:85034 - en:snacks - 97.22%
row:85035 - en:snacks - 99.71%
row:85036 - en:dairies - 97.6%
row:85037 - en:fermented-foods - 99.85%
row:85038 - en:dairies - 96.99%
row:85039 - en:breads - 99.82%
row:85040 - en:eggs - 99.01%
row:85041 - en:grated-carrots - 99.93%
row:85042 - en:snacks - 98.82%
row:85043 - en:snacks - 99.89%
row:85044 - en:spreadable-fats - 98.77%
row:85045 - en:snacks - 97.92%
row:85046 - en:biscuits-and-cakes - 91.58%
row:85047 - en:sweeteners - 77.38%
row:85048 - en:meat-based-products - 91.47%
row:85049 - en:beverages - 99.94%
row:85050 - en:meats - 99.84%
row:85051 - en:meals - 85.13%
row:85052 - en:condiments - 92.57%
row:85053 - en:prepa

row:86799 - en:sweet-snacks - 95.33%
row:86800 - en:breads - 99.84%
row:86801 - en:confectioneries - 99.99%
row:86802 - en:fruit-and-vegetable-preserves - 99.57%
row:86803 - en:meats - 76.81%
row:86804 - en:biscuits-and-cakes - 94.41%
row:86805 - en:meats - 99.85%
row:86806 - en:meals - 53.75%
row:86807 - en:plant-based-foods - 68.92%
row:86808 - en:snacks - 95.26%
row:86809 - en:snacks - 99.25%
row:86810 - en:plant-based-foods-and-beverages - 99.94%
row:86811 - en:frozen-desserts - 99.21%
row:86812 - en:meats - 91.04%
row:86813 - en:groceries - 99.92%
row:86814 - en:dairies - 99.96%
row:86815 - en:sweet-snacks - 99.0%
row:86816 - en:fermented-foods - 99.91%
row:86817 - en:snacks - 99.89%
row:86818 - en:cereals-and-potatoes - 65.91%
row:86819 - en:groceries - 60.52%
row:86820 - en:plant-based-foods-and-beverages - 99.12%
row:86821 - en:snacks - 98.06%
row:86822 - en:fermented-foods - 99.96%
row:86823 - en:plant-based-foods-and-beverages - 96.79%
row:86824 - en:plant-based-foods - 83.44

In [26]:
# val data predictions
import numpy as np
argmaxes=np.argmax(y_pred_val ,axis=1)

r=0
for i in argmaxes:
    print(f'row:{r} - {category_vocab[i]} - {round(y_pred_val[r,i]*100,2)}%')
    r+=1

row:0 - en:salts - 98.63%
row:1 - en:plant-based-foods-and-beverages - 85.63%
row:2 - en:beverages - 97.96%
row:3 - en:legume-milks - 86.33%
row:4 - en:nougats - 97.1%
row:5 - en:dairies - 99.62%
row:6 - en:meats - 85.57%
row:7 - en:dairies - 99.67%
row:8 - en:bee-products - 99.91%
row:9 - en:sweet-snacks - 81.68%
row:10 - en:vinegars - 96.17%
row:11 - en:beverages - 71.94%
row:12 - en:plant-based-foods-and-beverages - 86.88%
row:13 - en:snacks - 99.71%
row:14 - en:cereals-and-potatoes - 98.91%
row:15 - en:desserts - 99.78%
row:16 - en:plant-based-foods - 97.79%
row:17 - en:confectioneries - 97.78%
row:18 - en:snacks - 97.17%
row:19 - en:beverages - 98.2%
row:20 - en:meals - 87.79%
row:21 - en:canned-common-beans - 97.92%
row:22 - en:beverages - 98.97%
row:23 - en:snacks - 99.73%
row:24 - en:snacks - 95.63%
row:25 - en:fermented-foods - 99.14%
row:26 - en:meals - 96.06%
row:27 - en:snacks - 97.06%
row:28 - en:sweeteners - 99.55%
row:29 - en:frozen-foods - 92.02%
row:30 - en:sweet-fritt

row:1584 - en:plant-based-foods - 97.73%
row:1585 - en:plant-based-foods - 99.89%
row:1586 - en:fats - 99.74%
row:1587 - en:plant-based-foods-and-beverages - 99.91%
row:1588 - en:snails - 94.09%
row:1589 - en:fruits-based-foods - 54.77%
row:1590 - en:plant-based-foods-and-beverages - 99.89%
row:1591 - en:snacks - 93.73%
row:1592 - en:beverages - 99.06%
row:1593 - en:ground-steaks - 93.85%
row:1594 - en:beverages - 98.89%
row:1595 - en:dairies - 95.35%
row:1596 - en:plant-based-foods-and-beverages - 99.99%
row:1597 - en:cheeses - 99.93%
row:1598 - en:beverages - 94.23%
row:1599 - en:plant-based-foods - 78.92%
row:1600 - en:compotes - 96.38%
row:1601 - en:snacks - 99.44%
row:1602 - en:snacks - 96.13%
row:1603 - en:snacks - 99.97%
row:1604 - en:plant-based-foods - 92.36%
row:1605 - en:snacks - 69.71%
row:1606 - en:dairies - 98.43%
row:1607 - en:meals - 86.42%
row:1608 - en:sweet-spreads - 99.63%
row:1609 - en:snacks - 97.82%
row:1610 - en:beverages - 98.96%
row:1611 - en:groceries - 96.91

row:3083 - en:meats - 99.34%
row:3084 - en:canned-plant-based-foods - 98.63%
row:3085 - en:biscuits-and-cakes - 96.54%
row:3086 - en:dairies - 99.91%
row:3087 - en:beverages - 93.97%
row:3088 - en:cereals-and-potatoes - 98.77%
row:3089 - en:snacks - 94.42%
row:3090 - en:desserts - 88.31%
row:3091 - en:sweet-snacks - 99.59%
row:3092 - en:beverages - 99.97%
row:3093 - en:groceries - 61.72%
row:3094 - en:groceries - 99.23%
row:3095 - en:plant-based-foods-and-beverages - 77.11%
row:3096 - en:snacks - 43.3%
row:3097 - en:dairies - 99.04%
row:3098 - en:groceries - 99.81%
row:3099 - en:sweet-snacks - 97.04%
row:3100 - en:alcoholic-beverages - 99.5%
row:3101 - en:beverages - 98.94%
row:3102 - en:mackerels - 99.58%
row:3103 - en:dairies - 93.65%
row:3104 - en:chips-and-fries - 97.87%
row:3105 - en:sweet-spreads - 99.39%
row:3106 - en:sauces - 95.19%
row:3107 - en:seafood - 99.47%
row:3108 - en:snacks - 77.57%
row:3109 - en:cheeses - 89.8%
row:3110 - en:cereals-and-potatoes - 79.28%
row:3111 - e

row:4583 - en:plant-based-foods - 88.42%
row:4584 - en:groceries - 99.54%
row:4585 - en:plant-based-foods-and-beverages - 99.76%
row:4586 - en:crepes-and-galettes - 98.9%
row:4587 - en:plant-based-foods-and-beverages - 99.96%
row:4588 - en:biscuits-and-cakes - 93.44%
row:4589 - en:snacks - 94.77%
row:4590 - en:spreadable-fats - 98.36%
row:4591 - en:plant-based-foods - 98.12%
row:4592 - en:meats - 99.73%
row:4593 - en:meals - 91.47%
row:4594 - en:plant-based-foods-and-beverages - 97.15%
row:4595 - en:plant-based-foods - 94.31%
row:4596 - en:sandwiches - 34.77%
row:4597 - en:plant-based-foods-and-beverages - 67.71%
row:4598 - en:desserts - 99.59%
row:4599 - en:advent-calendars - 99.37%
row:4600 - en:fermented-foods - 99.76%
row:4601 - en:plant-based-foods-and-beverages - 99.17%
row:4602 - en:biscuits-and-cakes - 99.41%
row:4603 - en:meats - 99.34%
row:4604 - en:yule-log - 95.72%
row:4605 - en:harissa-sauces - 98.83%
row:4606 - en:plant-based-foods - 83.48%
row:4607 - en:dairies - 99.8%
r

row:6082 - en:plant-based-foods - 98.38%
row:6083 - en:plant-based-foods - 98.28%
row:6084 - en:sweet-spreads - 99.82%
row:6085 - en:meat-analogues - 92.49%
row:6086 - en:fats - 95.35%
row:6087 - en:fermented-milk-products - 99.8%
row:6088 - en:meats - 86.8%
row:6089 - en:seafood - 99.85%
row:6090 - en:meals - 60.93%
row:6091 - en:beverages - 98.05%
row:6092 - en:beverages - 17.96%
row:6093 - en:fruit-curds - 89.54%
row:6094 - en:alcoholic-beverages - 93.23%
row:6095 - en:biscuits-and-cakes - 85.37%
row:6096 - en:sauces - 99.57%
row:6097 - en:dairies - 97.16%
row:6098 - en:meats - 100.0%
row:6099 - en:poultries - 40.68%
row:6100 - en:meats - 93.02%
row:6101 - en:meats - 83.01%
row:6102 - en:meats - 99.25%
row:6103 - en:plant-based-foods - 99.61%
row:6104 - en:alcoholic-beverages - 99.51%
row:6105 - en:kiwifruits - 99.34%
row:6106 - en:pizzas-pies-and-quiches - 99.24%
row:6107 - en:frozen-desserts - 99.53%
row:6108 - en:plant-based-foods-and-beverages - 94.47%
row:6109 - en:sauces - 89.

...

row:80005 - en:plant-based-foods - 66.78%
row:80006 - en:meats - 97.24%
row:80007 - en:dairies - 92.89%
row:80008 - en:spreadable-fats - 95.07%
row:80009 - en:seafood - 99.83%
row:80010 - en:snacks - 96.15%
row:80011 - en:plant-based-beverages - 77.12%
row:80012 - en:meats - 95.5%
row:80013 - en:trouts - 99.42%
row:80014 - en:meats - 95.73%
row:80015 - en:beverages - 99.82%
row:80016 - en:confectioneries - 99.94%
row:80017 - en:plant-based-foods-and-beverages - 91.09%
row:80018 - en:fermented-foods - 99.01%
row:80019 - en:snacks - 98.17%
row:80020 - en:fermented-foods - 98.65%
row:80021 - en:biscuits-and-cakes - 94.77%
row:80022 - en:breads - 98.59%
row:80023 - en:cheeses - 100.0%
row:80024 - en:fermented-foods - 95.57%
row:80025 - en:breads - 95.55%
row:80026 - en:seafood - 90.44%
row:80027 - en:snacks - 98.45%
row:80028 - en:plant-based-foods - 80.8%
row:80029 - en:biscuits-and-cakes - 93.88%
row:80030 - en:canned-common-beans - 92.53%
row:80031 - en:beverages - 99.42%
row:80032 - en

row:81561 - en:snacks - 67.74%
row:81562 - en:cereals-and-their-products - 97.45%
row:81563 - en:biscuits-and-cakes - 98.39%
row:81564 - en:fermented-foods - 93.06%
row:81565 - en:plant-milks - 79.89%
row:81566 - en:plant-based-foods-and-beverages - 98.8%
row:81567 - en:compotes - 97.59%
row:81568 - en:beverages - 80.32%
row:81569 - en:viennoiseries - 98.73%
row:81570 - en:plant-based-foods-and-beverages - 94.77%
row:81571 - en:snacks - 78.57%
row:81572 - en:meals - 22.53%
row:81573 - en:meats - 99.47%
row:81574 - en:plant-based-foods - 71.05%
row:81575 - en:dairies - 93.84%
row:81576 - en:beverages - 99.66%
row:81577 - en:beverages - 99.46%
row:81578 - en:biscuits-and-cakes - 61.28%
row:81579 - en:plant-based-foods - 59.05%
row:81580 - en:sauces - 55.46%
row:81581 - en:fermented-milk-products - 96.74%
row:81582 - en:non-food-products - 42.49%
row:81583 - en:sauces - 97.91%
row:81584 - en:snacks - 99.72%
row:81585 - en:white-meat-rillettes - 99.81%
row:81586 - en:fats - 97.09%
row:8158

row:83280 - en:groceries - 97.33%
row:83281 - en:dairies - 99.78%
row:83282 - en:beverages - 45.04%
row:83283 - en:snacks - 87.14%
row:83284 - en:plant-based-foods-and-beverages - 97.26%
row:83285 - en:dietary-supplements - 70.84%
row:83286 - en:prepared-meats - 96.03%
row:83287 - en:plant-based-foods-and-beverages - 57.47%
row:83288 - en:terrines - 95.51%
row:83289 - en:sauces - 85.56%
row:83290 - en:alcoholic-beverages - 79.83%
row:83291 - en:sweet-snacks - 98.62%
row:83292 - en:compotes - 91.13%
row:83293 - en:sandwiches - 99.8%
row:83294 - en:plant-based-foods-and-beverages - 99.98%
row:83295 - en:meats - 52.84%
row:83296 - en:sweet-spreads - 99.45%
row:83297 - en:cheeses - 97.95%
row:83298 - en:beverages - 99.13%
row:83299 - en:dairies - 6.86%
row:83300 - en:meals - 97.33%
row:83301 - en:confectioneries - 98.92%
row:83302 - en:sweet-spreads - 99.89%
row:83303 - en:waters - 98.58%
row:83304 - en:plant-based-foods-and-beverages - 97.58%
row:83305 - en:snacks - 99.74%
row:83306 - en:

row:84973 - en:plant-based-foods-and-beverages - 98.59%
row:84974 - en:simple-syrups - 98.2%
row:84975 - en:desserts - 90.56%
row:84976 - en:cereals-and-potatoes - 57.27%
row:84977 - en:canned-common-beans - 97.07%
row:84978 - en:breads - 96.64%
row:84979 - en:beverages - 98.53%
row:84980 - en:seafood - 93.6%
row:84981 - en:meals - 42.95%
row:84982 - en:snacks - 96.1%
row:84983 - en:plant-based-foods - 58.95%
row:84984 - en:dairies - 89.26%
row:84985 - en:plant-based-foods - 99.61%
row:84986 - en:cakes - 90.34%
row:84987 - en:dairies - 98.25%
row:84988 - en:snacks - 99.66%
row:84989 - en:syrups - 64.03%
row:84990 - en:beverages - 99.29%
row:84991 - en:dairies - 99.98%
row:84992 - en:breads - 99.61%
row:84993 - en:nuts-and-their-products - 69.89%
row:84994 - en:meals - 91.89%
row:84995 - en:meals - 48.53%
row:84996 - en:plant-based-foods-and-beverages - 92.32%
row:84997 - en:fishes - 99.64%
row:84998 - en:plant-based-foods-and-beverages - 95.8%
row:84999 - en:snacks - 94.75%
row:85000 -

row:86771 - en:alcoholic-beverages - 93.53%
row:86772 - en:sauces - 97.37%
row:86773 - en:meats - 97.37%
row:86774 - en:groceries - 98.36%
row:86775 - en:meats - 99.34%
row:86776 - en:fermented-foods - 99.95%
row:86777 - en:fermented-foods - 90.31%
row:86778 - en:beverages - 96.53%
row:86779 - en:fermented-foods - 97.94%
row:86780 - en:dairies - 99.99%
row:86781 - en:breads - 99.72%
row:86782 - en:biscuits-and-cakes - 99.38%
row:86783 - en:plant-based-foods-and-beverages - 98.48%
row:86784 - en:meals - 82.44%
row:86785 - en:meats - 99.5%
row:86786 - en:simple-syrups - 99.44%
row:86787 - en:snacks - 98.98%
row:86788 - en:plant-based-foods-and-beverages - 98.01%
row:86789 - en:tartlets - 95.13%
row:86790 - en:ground-meat-preparations - 83.29%
row:86791 - en:plant-based-foods - 28.72%
row:86792 - en:beverages - 98.74%
row:86793 - en:plant-based-foods - 99.18%
row:86794 - en:dairies - 99.9%
row:86795 - en:fruits-and-vegetables-based-foods - 93.64%
row:86796 - en:condiments - 99.62%
row:867

In [58]:
from sklearn.metrics import accuracy_score
# accuracy_score is for a classification model
accuracy_score(y_pred_test,y_pred_val)

ValueError: continuous-multioutput is not supported

Error occurs due to continuous values

## Explore dataset

In [19]:
import pandas as pd
from robotoff.utils import gzip_jsonl_iter
import pathlib

import settings
from typing import Any, Callable, Dict, Iterable, Optional, List

def create_dataframe(split: str, lang: str) -> pd.DataFrame:
     if split not in ("train", "test", "val"):
         raise ValueError("split must be either 'train', 'test' or 'val'")

     file_name = "category_{}.{}.jsonl.gz".format(lang, split)
     full_path = settings.DATA_DIR / file_name
     return pd.DataFrame(iter_product(full_path))

def count_categories(df: pd.DataFrame) -> Dict:
    categories_count = defaultdict(int)

    for categories in df.categories_tags:
        for category in categories:
            categories_count[category] += 1

    return categories_count

def iter_product(data_path: pathlib.Path):
    for product in gzip_jsonl_iter(data_path):
        product.pop("images", None)

        if "nutriments" in product:
            nutriments = product["nutriments"] or {}

        yield product

In [21]:
training_ds = create_dataframe("train", "xx")
test_ds = create_dataframe("test", "xx")
val_ds = create_dataframe("val", "xx")

In [22]:
val_ds.shape

(87434, 8)

In [24]:
val_ds.head(20)

code                                         nutriments  \
0   3183280018259  {'energy-kcal_value': 0, 'energy_value': 0, 'e...   
1   8690504270591  {'energy_unit': 'kcal', 'sodium': 0.2319999999...   
2   8719179003652  {'proteins': 0, 'nutrition-score-fr_100g': 1, ...   
3   4316268502504  {'energy_value': 59, 'energy_unit': 'kcal', 's...   
4   3770011407224                                               None   
5        22472212  {'sugars_100g': 4.2, 'fat_value': 4.9, 'sodium...   
6   0829005000170  {'cholesterol': 0.058, 'vitamin-a_unit': 'IU',...   
7     07078401672  {'calcium_serving': 0.2, 'trans-fat': 0, 'carb...   
8   3760005727759  {'fat_value': 0, 'sugars_100g': 0, 'sodium_val...   
9   8437009284049  {'salt': 0.22, 'sugars': 46, 'cocoa': 38, 'pro...   
10  3596710091546  {'saturated-fat_value': 0.05, 'sugars_value': ...   
11  3760056350166  {'alcohol_unit': '% vol', 'fruits-vegetables-n...   
12  3250390272151  {'energy': 343, 'fat_unit': '', 'salt_value': ...   
13  5000357103350  {'sodium_100g': 0, 'nova-group': 4, 'saturated...   
14  8003007818656  {'fat_value': 1.7, 'sugars_100g': 1.7, 'sodium...   
15  0753611001194  {'sodium': 0.057, 'fiber_100g': 0, 'nova-group...   
16  3083680482370  {'proteins_100g': 1, 'sodium_value': 0.02, 'fa...   
17  0075450083187  {'energy_value': 321, 'energy-kcal_serving': 8...   
18  0791080998768  {'saturated-fat_serving': 4, 'iron_value': 0.8...   
19  0802763140548  {'manganese_unit': 'mg', 'iron_value': 0.22, '...   

                                         product_name  \
0                                        Fleur de sel   
1                                           coco pops   
2   Thé épicé Dreaming camomille, lavande & valériane   
3                                  Soja Vanille Drink   
4                          Nougat au miel de Bretagne   
5                     Yaourt Nature au lait de Chèvre   
6                  Carne asada seasoned outside skirt   
7                                Sharp cheddar cheese   
8                                      Miel de fleurs   
9                                    Caramalized nutd   
10                                  Vinaigre d'alcool   
11                               Duchesse de Lorraine   
12                                            Compote   
13                       Pastilles Menthe sans sucres   
14                                              Gigli   
15  San Bernardo, Premium Ice Cream, Guava & Cream...   
16                                 Composée Croquante   
17                                 Jumbo marshmallows   
18  Anette's Chocolates, Micro Brew Brittle Beer C...   
19                                        Prune Juice   

                                      categories_tags  \
0   [en:groceries, en:condiments, en:sea-salts, en...   
1   [en:plant-based-foods-and-beverages, en:cereal...   
2   [en:plant-based-foods-and-beverages, en:hot-be...   
3   [en:plant-based-foods-and-beverages, en:soy-mi...   
4   [en:nougats, en:confectioneries, en:sweet-snac...   
5   [en:fermented-foods, en:fermented-milk-product...   
6                                          [en:meats]   
7   [en:fermented-foods, en:cheeses, en:fermented-...   
8   [en:spreads, en:sweet-spreads, en:bee-products...   
9   [en:snacks, en:cocoa-and-its-products, en:milk...   
10                 [en:alcohol-vinegars, en:vinegars]   
11   [en:beers, en:beverages, en:alcoholic-beverages]   
12  [en:fruits-and-vegetables-based-foods, en:dess...   
13  [en:candies, en:confectioneries, en:sweet-snac...   
14  [en:plant-based-foods-and-beverages, en:pastas...   
15  [en:desserts, en:frozen-foods, en:frozen-desse...   
16  [en:fruits-and-vegetables-based-foods, en:plan...   
17   [en:confectioneries, en:sweet-snacks, en:snacks]   
18  [en:snacks, en:cocoa-and-its-products, en:choc...   
19  [en:plant-based-foods-and-beverages, en:bevera...   

                                      ingredient_tags  \
0                                              